In [6]:
import xlsxwriter

In [7]:
from repytex.tools.evaluation import Evaluation
from repytex.tools.sqlite_getters import all_ev_description
import sqlite3

In [8]:
conn = sqlite3.connect('./recopytex.db')

In [9]:
all_ev_description(conn)

id                name  term  t_id
0    1   DS1 mise en jambe     1     1
1    2                 DS1     1     2
2    3                 DS1     1     3
3    4                 DS2     1     2
4    5                 DS2     1     1
5    6                 DS2     1     3
6    7                 DS3     1     3
7    8  Pyramide de pièces     1     1
8    9                 DS3     1     2
9   10                 DS3     1     1
10  11                 DS4     2     3
11  13                 DS5     2     3
12  14             DM noel     2     1
13  15             DM noel     2     2
14  16                 DS4     2     1
15  17                 DS4     2     2
16  18                 DS6     2     3
17  19                 CM1     2     2
18  20          DNB blanc1     2     2
19  21          DNB blanc1     2     1

In [10]:
ev = Evaluation.from_sqlite(21, conn)

In [11]:
ev.name

'DNB blanc1'

In [12]:
ev.ex_df

id                     name  eval_id                        date comment
0  64                  1 - QCM       21  2018-02-07 00:00:00.000000        
1  65    2 - Boite de chocolat       21  2018-02-07 00:00:00.000000        
2  66              3 - Scratch       21  2018-02-07 00:00:00.000000        
3  67  4 - Programme de calcul       21  2018-02-07 00:00:00.000000        
4  68              5 - Macaron       21  2018-02-07 00:00:00.000000        
5  69           6 - Inspecteur       21  2018-02-07 00:00:00.000000        
6  70             7 - La tache       21  2018-02-07 00:00:00.000000

In [9]:
wb = xlsxwriter.Workbook("DNB_BLANC_pro1.xlsx")

Formatages

In [10]:
eval_format = wb.add_format({'bold': True, 'font_color': 'red'})
eval_cell = wb.add_format()
eval_cell.set_bg_color("red")
# exo_cell

La feuille de calcul

In [11]:
wb = xlsxwriter.Workbook("DS4_302.xlsx")

In [12]:
ws = wb.add_worksheet()

En tête du tableau

In [13]:
ws.write(0,1,"Competence")
ws.write(0,2,"Barème")

0

Toutes les questions et exercices

In [14]:
def q_line(q, row, ws):
    ws.write(row, 0, f"{q.name} - {q.comment}")
    ws.write(row, 1, f"{q.competence}")
    ws.write(row, 2, q.score_rate)

In [15]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.write(row, 0, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+2, qrow+2)])
    for i in range(30):
        ws.write(row, i+2, f"=SUM({row_range})")
    return qrow

In [16]:
row = 2
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
ws.write(1,0, ev.name, eval_format)
exo_xls_range = ", ".join([f"C{i+1}" for i in exo_rows])
for i in range(30):
    ws.write(1,i+2, f"=SUM({exo_xls_range})", eval_format)

In [17]:
wb.close()

# Avec openpyxl

In [13]:
from openpyxl import Workbook
from openpyxl.styles import PatternFill, Border, Side, Alignment, Protection, Font, colors

In [14]:
colors.RED

'00FF0000'

In [15]:
wb = Workbook()

In [16]:
ws = wb.create_sheet(ev.name)

In [17]:
ws.cell(1,2,"Competence")
ws.cell(1,3,"Barème")

<Cell 'DNB blanc1'.C1>

In [18]:
def q_line(q, row, ws):
    ws.cell(row, 1, f"{q.name} - {q.comment}")
    ws.cell(row, 2, f"{q.competence}")
    ws.cell(row, 3, q.score_rate)

In [19]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.cell(row, 1, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+1, qrow+1)])
    ws.cell(row, 3, f"=SUM({row_range})")
    return qrow

In [20]:
row = 3
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
eval_row = ws.row_dimensions[2]
eval_row.fill = PatternFill(bgColor=colors.RED)
ws.cell(2,1, ev.name)
exo_xls_range = ", ".join([f"C{i}" for i in exo_rows])
ws.cell(2,3, f"=SUM({exo_xls_range})")

<Cell 'DNB blanc1'.C2>

In [21]:
ev.tribe

'302'

In [22]:
wb.save(f"./{ev.name}-{ev.tribe}.xlsx")